In [1]:
import trimesh
import numpy as np
import os
from torch import optim, nn, utils, Tensor
import lightning as L
from pytorch3d.structures import Meshes
import mano
from network.softNet import softNet
from torch.utils.data import DataLoader
import torch
import trimesh
import numpy as np
from utils import utils_loss
import math
# 读取两个网格
meshA = trimesh.load('./vis_deform/hand_0_1.ply')
meshB = trimesh.load('./vis_deform/obj_0_1.ply')
obj_mean = meshB.vertices.mean(axis=0)
print(obj_mean)
meshB.vertices -= obj_mean
meshA.vertices -= obj_mean

obj_mean = meshB.vertices.mean(axis=0)
print(obj_mean)

meshB.vertices = meshB.vertices
# 计算meshA中每个顶点到meshB的最小距离
distances = meshB.nearest.on_surface(meshA.vertices)[1]

# 找到最深穿入点（距离最小的点）
deepest_point_index = np.argmin(distances)
deepest_point = meshA.vertices[deepest_point_index]
print(distances[deepest_point_index])
trimesh.Scene([meshA, meshB]).show()

/home/zhaozhe/miniconda3/envs/pointcept/lib/python3.8/site-packages/requests/__init__.py:109: RequestsDependencyWarning: urllib3 (2.2.1) or chardet (None)/charset_normalizer (3.3.2) doesn't match a supported version!
  warnings.warn(


[-2.15064407e-04  5.89553241e-05  1.71378632e-04]
[-3.06136305e-16 -7.39280015e-16 -4.01937210e-16]
1.4409687786002961e-05


In [2]:

def find_point_distances(meshA, meshB,contact_map_bool):
    # 将mesh转换为点云和法线
    verticesA = torch.tensor(meshA.vertices, dtype=torch.float32)
    normalsA = torch.tensor(meshA.vertex_normals, dtype=torch.float32)*-1
    verticesB = torch.tensor(meshB.vertices, dtype=torch.float32)
    
    # 创建一个空的三角形光线拦截器
    ray_intersector = trimesh.ray.ray_pyembree.RayMeshIntersector(meshB)
    
    # 初始化距离张量
    distances = torch.full((verticesA.shape[0],), float(0), dtype=torch.float32)
    
    # 遍历meshA中的每个点
    for i, (point, normal) in enumerate(zip(verticesA, normalsA)):
            # 创建从该点出发的射线，方向为法线方向
            ray_origins = point.unsqueeze(0).numpy()
            ray_directions = normal.unsqueeze(0).numpy()
            
            # 计算射线与meshB的交点
            locations, index_ray, index_tri = ray_intersector.intersects_location(ray_origins, ray_directions)
            
            # 如果有交点，计算距离
            if len(locations) > 0:
                # 取第一个交点（假设只有一个交点）
                intersection_point = torch.tensor(locations[0], dtype=torch.float32)
                distance = torch.norm(intersection_point - point)
                distances[i] = distance
    return distances



def batched_index_select(input, index, dim=1):
    '''
    :param input: [B, N1, *]
    :param dim: the dim to be selected
    :param index: [B, N2]
    :return: [B, N2, *] selected result
    '''
    views = [input.size(0)] + [1 if i != dim else -1 for i in range(1, len(input.shape))]
    expanse = list(input.shape)
    expanse[0] = -1
    expanse[dim] = -1
    index = index.view(views).expand(expanse)
    return torch.gather(input, dim=dim, index=index)

def get_faces_xyz(faces_idx, xyz):
    '''
    :param faces_idx: [B, N1, 3]. N1 is number of faces (1538 for MANO), index of face vertices in N2
    :param xyz: [B, N2, 3]. N2 is number of points.
    :return: faces_xyz: [B, N1, 3, 3] faces vertices coordinate
    '''
    B, N1, D = faces_idx.size()
    N2 = xyz.size(1)
    xyz_replicated = xyz.cpu().unsqueeze(1).repeat(1,N1,1,1)  # use cpu to save CUDA memory
    faces_idx_replicated = faces_idx.unsqueeze(-1).repeat(1,1,1,D).type(torch.LongTensor)
    return torch.gather(xyz_replicated, dim=2, index=faces_idx_replicated).to(faces_idx.device)

def batch_mesh_contains_points(
    ray_origins, # point cloud as origin of rays
    obj_triangles,
    direction=torch.Tensor([0.4395064455, 0.617598629942, 0.652231566745]),
):
    """Times efficient but memory greedy !
    Computes ALL ray/triangle intersections and then counts them to determine
    if point inside mesh
    Args:
    ray_origins: (batch_size x point_nb x 3)
    obj_triangles: (batch_size, triangle_nb, vertex_nb=3, vertex_coords=3)
    tol_thresh: To determine if ray and triangle are //
    Returns:
    exterior: (batch_size, point_nb) 1 if the point is outside mesh, 0 else
    """
    tol_thresh = 0.0000001
    batch_size = obj_triangles.shape[0]
    triangle_nb = obj_triangles.shape[1]
    point_nb = ray_origins.shape[1]

    # Batch dim and triangle dim will flattened together
    batch_points_size = batch_size * triangle_nb
    # Direction is random but shared
    v0, v1, v2 = obj_triangles[:, :, 0], obj_triangles[:, :, 1], obj_triangles[:, :, 2]
    # Get edges
    v0v1 = v1 - v0
    v0v2 = v2 - v0

    direction = direction.to(ray_origins.device)
    # Expand needed vectors
    batch_direction = direction.view(1, 1, 3).expand(batch_size, triangle_nb, 3)

    # Compute ray/triangle intersections
    pvec = torch.cross(batch_direction, v0v2, dim=2)
    dets = torch.bmm(
        v0v1.view(batch_points_size, 1, 3), pvec.view(batch_points_size, 3, 1)
    ).view(batch_size, triangle_nb)

    # Check if ray and triangle are parallel
    parallel = abs(dets) < tol_thresh
    invdet = 1 / (dets + 0.1 * tol_thresh)

    # Repeat mesh info as many times as there are rays
    triangle_nb = v0.shape[1]
    v0 = v0.repeat(1, point_nb, 1)
    v0v1 = v0v1.repeat(1, point_nb, 1)
    v0v2 = v0v2.repeat(1, point_nb, 1)
    hand_verts_repeated = (
        ray_origins.view(batch_size, point_nb, 1, 3)
        .repeat(1, 1, triangle_nb, 1)
        .view(ray_origins.shape[0], triangle_nb * point_nb, 3)
    )
    pvec = pvec.repeat(1, point_nb, 1)
    invdet = invdet.repeat(1, point_nb)
    tvec = hand_verts_repeated - v0
    u_val = (
        torch.bmm(
            tvec.view(batch_size * tvec.shape[1], 1, 3),
            pvec.view(batch_size * tvec.shape[1], 3, 1),
        ).view(batch_size, tvec.shape[1])
        * invdet
    )
    # Check ray intersects inside triangle
    u_correct = (u_val > 0) * (u_val < 1)
    qvec = torch.cross(tvec, v0v1, dim=2)

    batch_direction = batch_direction.repeat(1, point_nb, 1)
    v_val = (
        torch.bmm(
            batch_direction.view(batch_size * qvec.shape[1], 1, 3),
            qvec.view(batch_size * qvec.shape[1], 3, 1),
        ).view(batch_size, qvec.shape[1])
        * invdet
    )
    v_correct = (v_val > 0) * (u_val + v_val < 1)
    t = (
        torch.bmm(
            v0v2.view(batch_size * qvec.shape[1], 1, 3),
            qvec.view(batch_size * qvec.shape[1], 3, 1),
        ).view(batch_size, qvec.shape[1])
        * invdet
    )
    # Check triangle is in front of ray_origin along ray direction
    t_pos = t >= tol_thresh
    parallel = parallel.repeat(1, point_nb)
    # # Check that all intersection conditions are met
    try:
        not_parallel = 1 - parallel
    except:
        not_parallel = parallel==False
    final_inter = v_correct * u_correct * not_parallel * t_pos
    # Reshape batch point/vertices intersection matrix
    # final_intersections[batch_idx, point_idx, triangle_idx] == 1 means ray
    # intersects triangle
    final_intersections = final_inter.view(batch_size, point_nb, triangle_nb)
    # Check if intersection number accross mesh is odd to determine if point is
    # outside of mesh
    exterior = final_intersections.sum(2) % 2 == 0
    return exterior
def get_NN(src_xyz, trg_xyz, k=1):
    '''
    :param src_xyz: [B, N1, 3]
    :param trg_xyz: [B, N2, 3]
    :return: nn_dists, nn_dix: all [B, 3000] tensor for NN distance and index in N2
    '''
    B = src_xyz.size(0)
    src_lengths = torch.full(
        (src_xyz.shape[0],), src_xyz.shape[1], dtype=torch.int64, device=src_xyz.device
    )  # [B], N for each num
    trg_lengths = torch.full(
        (trg_xyz.shape[0],), trg_xyz.shape[1], dtype=torch.int64, device=trg_xyz.device
    )
    src_nn = knn_points(src_xyz, trg_xyz, lengths1=src_lengths, lengths2=trg_lengths, K=k)  # [dists, idx]
    nn_dists = src_nn.dists[..., 0]
    nn_idx = src_nn.idx[..., 0]
 
    return nn_dists, nn_idx


In [3]:
prior_idx=[
        697, 698, 699, 700, 712, 713, 714, 715, 737, 738, 739, 740, 741, 743, 744, 745, 746, 748, 749,
        750, 753, 754, 755, 756, 757, 758, 759, 760, 761, 762, 763, 764, 765, 766, 767, 768,
        46, 47, 48, 49, 164, 165, 166, 167, 194, 195, 223, 237, 238, 280, 281, 298, 301, 317, 320, 323, 324, 325, 326,
        327, 328, 329, 330, 331, 332, 333, 340, 341, 342, 343, 344, 345, 346, 347, 348, 349, 350, 351, 352, 353, 354,
        355,
        356, 357, 358, 359, 375, 376, 386, 387, 396, 397, 402, 403, 413, 429, 433, 434, 435, 436, 437, 438,
        439, 440, 441, 442, 443, 444, 452, 453, 454, 455, 456, 459, 460, 461, 462, 463, 464, 465, 466, 467,
        468, 469, 470, 471, 484, 485, 486, 496, 497, 506, 507, 513, 514, 524, 545, 546, 547, 548, 549,
        550, 551, 552, 553, 555, 563, 564, 565, 566, 567, 570, 572, 573, 574, 575, 576, 577, 578,
        580, 581, 582, 583, 600, 601, 602, 614, 615, 624, 625, 630, 631, 641, 663, 664, 665, 666, 667,
        668, 670, 672, 680, 681, 682, 683, 684, 686, 687, 688, 689, 690, 691, 692, 693, 694, 695,
        #73, 96, 98, 99, 772, 774, 775, 777
        ]
hand_vertices = meshA.vertices
mesh_ = Meshes(verts= torch.tensor(hand_vertices).unsqueeze(0), faces=torch.tensor(meshA.faces).unsqueeze(0))  
hand_normal = mesh_.verts_normals_packed().view(-1, 778, 3)
hand_normal_prior = hand_normal[0][prior_idx].unsqueeze(0)

mesh_obj = Meshes(verts= torch.tensor( meshB.vertices).unsqueeze(0), faces=torch.tensor(meshB.faces).unsqueeze(0))  
obj_normal = mesh_obj.verts_normals_packed().view(1,-1, 3)

hand_vertices_prior = torch.tensor(hand_vertices[prior_idx]).float().unsqueeze(0)
obj_nn_dist_recon, obj_nn_idx_recon = utils_loss.get_NN(torch.tensor(meshB.vertices).unsqueeze(0).float(), hand_vertices_prior)
print(obj_nn_dist_recon.size())
interior = utils_loss.get_interior(hand_normal_prior, hand_vertices_prior, torch.tensor(meshB.vertices).unsqueeze(0).float(), obj_nn_idx_recon).type(torch.bool)
NN_src_xyz = batched_index_select(hand_vertices_prior, obj_nn_idx_recon)  # [B, 3000, 3]\
print(NN_src_xyz.size())
NN_vector = NN_src_xyz - torch.tensor(meshB.vertices).unsqueeze(0).float()  # [B, 3000, 3]
# get surface normal of NN src xyz for every trg xyz, should be a [B, 3000, 3] vector
NN_src_normal = batched_index_select(hand_normal_prior, obj_nn_idx_recon)
#interior = interior。float
print((NN_vector * NN_src_normal).size())
d = (NN_vector * NN_src_normal).sum(dim=-1)
hand_nn_dist_recon, hand_nn_idx_recon = utils_loss.get_NN( torch.tensor(meshA.vertices).unsqueeze(0).float(),torch.tensor(meshB.vertices).unsqueeze(0).float())



contact_map_bool_hand = (hand_nn_dist_recon<3e-4).float()
interior_hand = utils_loss.get_interior(obj_normal, torch.tensor(meshB.vertices).unsqueeze(0).float(), torch.tensor(meshA.vertices).unsqueeze(0).float(), hand_nn_idx_recon).type(torch.bool)
contact_map_bool_hand[interior_hand] =  (contact_map_bool_hand[interior_hand]*-1).float()
interior_f = torch.zeros(torch.tensor(meshB.vertices).size(0)) 
print(interior_f .size())
print(hand_nn_dist_recon .size())
interior_f[hand_nn_idx_recon.squeeze(0)] = hand_nn_dist_recon.squeeze(1)
print(interior_f)


max_idx = torch.argmax(d)
print(meshB.vertices[max_idx])
hand_id = obj_nn_idx_recon[0][max_idx]
print(hand_id)
print(max_idx)
max_d = d[0][max_idx]
print(max_d)
contact_map_bool = (obj_nn_dist_recon<3e-4).float()

 
obj_nn_dist_recon[interior]= obj_nn_dist_recon[interior]*-1
contact_map = obj_nn_dist_recon
print(contact_map_bool[interior].sum())
contact_map_bool[interior] = (contact_map_bool[interior]*-1).float()
contact_map = contact_map *abs(contact_map_bool)

torch.Size([1, 9740])
torch.Size([1, 9740, 3])
torch.Size([1, 9740, 3])
torch.Size([9740])
torch.Size([1, 778])
tensor([0., 0., 0.,  ..., 0., 0., 0.])
[0.0240365  0.05655572 0.03031521]
tensor(10)
tensor(8477)
tensor(0.0137, dtype=torch.float64)
tensor(276.)


In [4]:
colors = np.ones((len(meshA.vertices), 4)) * [1, 1, 1, 1]  # RGBA 白色
colors[prior_idx[hand_id]] = [1, 0, 0, 1]  # RGBA 红色
# 更新 mesh 的顶点颜色
meshA.visual.vertex_colors = colors
trimesh.Scene([meshA]).show()

In [5]:
colors = np.ones((len(meshB.vertices), 4)) * [1, 1, 1, 1]  # RGBA 白色
colors[abs(contact_map_bool).cpu().detach().bool().squeeze(0)] = [0, 0, 1, 1]  
colors[(contact_map_bool==-1).cpu().detach().bool().squeeze(0)] = [1, 0, 0, 1]  # RGBA 红色
colors[max_idx] = [0, 1, 0, 1]  # RGBA 红色
meshB.visual.vertex_colors = colors

colors = np.ones((len(meshA.vertices), 4)) * [1, 1, 1, 1]  # RGBA 白色
colors[abs(contact_map_bool_hand).cpu().detach().bool().squeeze(0)] = [0, 0, 1, 1]  
colors[(contact_map_bool_hand==-1).cpu().detach().bool().squeeze(0)] = [1, 0, 0, 1]  # RGBA 红色
meshA.visual.vertex_colors = colors
trimesh.Scene([meshB,meshA]).show()

In [6]:
trimesh.Scene([meshA]).show()

In [7]:
hand_vertices = meshA.vertices
mesh_obj = Meshes(verts= torch.tensor( meshB.vertices).unsqueeze(0), faces=torch.tensor(meshB.faces).unsqueeze(0))  
obj_normal = mesh_obj.verts_normals_packed().view(1,-1, 3)

hand_nn_dist_recon, hand_nn_idx_recon = utils_loss.get_NN( torch.tensor(meshA.vertices).unsqueeze(0).float(),torch.tensor(meshB.vertices).unsqueeze(0).float())
contact_map_bool_hand = (hand_nn_dist_recon<3e-4).float()
interior_hand = utils_loss.get_interior(obj_normal, torch.tensor(meshB.vertices).unsqueeze(0).float(), torch.tensor(meshA.vertices).unsqueeze(0).float(), hand_nn_idx_recon).type(torch.bool)
contact_map_bool_hand[interior_hand] =  (contact_map_bool_hand[interior_hand]*-1).float()
interior_f = torch.zeros(torch.tensor(meshB.vertices).size(0)) 
print(interior_f .size())
print(hand_nn_dist_recon .size())
interior_f[hand_nn_idx_recon.squeeze(0)] = hand_nn_dist_recon.squeeze(1)
print(interior_f)

for i in hand_nn_idx_recon:
    print(i)


mesh_ = Meshes(verts= torch.tensor(hand_vertices).unsqueeze(0), faces=torch.tensor(meshA.faces).unsqueeze(0))  
hand_normal = mesh_.verts_normals_packed().view(-1, 778, 3)
hand_normal_prior = hand_normal[0][(contact_map_bool_hand==-1).cpu().detach().bool().squeeze(0)].unsqueeze(0)



hand_vertices_prior = torch.tensor(hand_vertices[(contact_map_bool_hand==-1).cpu().detach().bool().squeeze(0)]).float().unsqueeze(0)
obj_nn_dist_recon, obj_nn_idx_recon = utils_loss.get_NN(torch.tensor(meshB.vertices).unsqueeze(0).float(), hand_vertices_prior)
print(obj_nn_dist_recon.size())
interior = utils_loss.get_interior(hand_normal_prior, hand_vertices_prior, torch.tensor(meshB.vertices).unsqueeze(0).float(), obj_nn_idx_recon).type(torch.bool)
NN_src_xyz = batched_index_select(hand_vertices_prior, obj_nn_idx_recon)  # [B, 3000, 3]\
print(NN_src_xyz.size())
NN_vector = NN_src_xyz - torch.tensor(meshB.vertices).unsqueeze(0).float()  # [B, 3000, 3]
# get surface normal of NN src xyz for every trg xyz, should be a [B, 3000, 3] vector
NN_src_normal = batched_index_select(hand_normal_prior, obj_nn_idx_recon)
#interior = interior。float
print((NN_vector * NN_src_normal).size())
d = (NN_vector * NN_src_normal).sum(dim=-1)




max_idx = torch.argmax(d)
print(meshB.vertices[max_idx])
hand_id = obj_nn_idx_recon[0][max_idx]
print(hand_id)
print(max_idx)
max_d = d[0][max_idx]
print(max_d)
contact_map_bool = (obj_nn_dist_recon<1e-4).float()

 
obj_nn_dist_recon[interior]= obj_nn_dist_recon[interior]*-1
contact_map = obj_nn_dist_recon
print(contact_map_bool[interior].sum())
contact_map_bool[interior] = (contact_map_bool[interior]*-1).float()
contact_map = contact_map *abs(contact_map_bool)

torch.Size([9740])
torch.Size([1, 778])
tensor([0., 0., 0.,  ..., 0., 0., 0.])
tensor([4993, 5188, 5690, 5297, 4447, 4445, 6297, 9355, 5501, 5777, 5601, 5300,
        5300, 9698, 5299, 5000, 3899, 3407, 9483, 4038, 2908, 3155, 9291, 3129,
        4034, 3869, 4002, 9620, 6407, 6100, 5601, 6407, 4130, 3865, 4129, 4130,
        4218, 4339, 4129, 4218, 4445, 4218, 4445, 6505, 3752, 3247, 5707, 9626,
        5307, 5706, 3128, 3248, 3380, 3247, 2875, 3248, 5800, 6013, 5905, 5800,
        5299, 4996, 5000, 4894, 9651, 9509, 3786, 3784, 4253, 4153, 3272, 3154,
        3021, 3151, 3410, 3282, 3031, 3028, 9604, 3502, 2257, 2017, 1733, 1860,
        3380, 3380, 5711, 5512, 4218, 6400, 4218, 4130, 4130, 4590, 4479, 4249,
        2903, 2630, 3133, 3017, 2016, 2142, 2018, 1732, 6721, 6099, 3247, 3502,
        3502, 4131, 4218, 9310, 4131, 4220, 4219, 5384, 4129, 4129, 4129, 3865,
        3752, 9604, 4129, 6298, 6400, 9110, 5990, 5002, 5204, 5302, 3757, 2875,
        4489, 5707, 5707, 5206, 5106, 437

In [8]:
colors = np.ones((len(meshB.vertices), 4)) * [1, 1, 1, 1]  # RGBA 白色
colors[abs(contact_map_bool).cpu().detach().bool().squeeze(0)] = [0, 0, 1, 1]  
colors[(contact_map_bool==-1).cpu().detach().bool().squeeze(0)] = [1, 0, 0, 1]  # RGBA 红色
colors[max_idx] = [0, 1, 0, 1]  # RGBA 红色
meshB.visual.vertex_colors = colors

colors = np.ones((len(meshA.vertices), 4)) * [1, 1, 1, 1]  # RGBA 白色
colors[abs(contact_map_bool_hand).cpu().detach().bool().squeeze(0)] = [0, 0, 1, 1]  
colors[(contact_map_bool_hand==-1).cpu().detach().bool().squeeze(0)] = [1, 0, 0, 1]  # RGBA 红色
meshA.visual.vertex_colors = colors
trimesh.Scene([meshB,meshA]).show()

In [9]:
trimesh.Scene([meshB]).show()

In [10]:
distance = find_point_distances(meshB,meshA,contact_map_bool[0])

tensor(0.0019)
tensor(0.0009)
tensor(0.0027)
tensor(0.0028)
tensor(0.0007)
tensor(0.0020)
tensor(0.0030)
tensor(0.0019)
tensor(0.0002)
tensor(0.0003)
tensor(0.0016)
tensor(0.0004)
tensor(0.0009)
tensor(0.0010)
tensor(0.0005)
tensor(0.0007)
tensor(0.0026)
tensor(0.0018)
tensor(0.0026)
tensor(0.0023)
tensor(0.0007)
tensor(0.0008)
tensor(0.0015)
tensor(0.0024)
tensor(0.0035)
tensor(0.0029)
tensor(0.0017)
tensor(0.0020)
tensor(0.0039)
tensor(0.0037)
tensor(0.0038)
tensor(0.0035)
tensor(0.0030)
tensor(0.0021)
tensor(0.0006)
tensor(0.0030)
tensor(0.0030)
tensor(0.0035)
tensor(0.0040)
tensor(0.0036)
tensor(0.0029)
tensor(0.0036)
tensor(0.0044)
tensor(0.0043)
tensor(0.0046)
tensor(0.0042)
tensor(0.0040)
tensor(0.0035)
tensor(0.0031)
tensor(0.0031)
tensor(0.0021)
tensor(0.0007)
tensor(0.0033)
tensor(0.0033)
tensor(0.0027)
tensor(0.0012)
tensor(0.0033)
tensor(0.0033)
tensor(0.0033)
tensor(0.0033)
tensor(0.0035)
tensor(0.0015)
tensor(0.0022)
tensor(0.0022)
tensor(0.0022)
tensor(0.0016)
tensor(0.0

In [11]:
colors = np.ones((len(meshB.vertices), 4)) * [1, 1, 1, 1]  # RGBA 白色
colors[abs(contact_map_bool).cpu().detach().bool().squeeze(0)] = [0, 0, 1, 1]  
colors[(contact_map_bool==-1).cpu().detach().bool().squeeze(0)] = [1, 0, 0, 1]  # RGBA 红色

distance = distance * (contact_map_bool==-1).float().squeeze(0)

sum = 0 
for i in range(0,distance.size(0)):
    if distance[i]>0 :#and distance[i]<1:
        print(distance[i])
        sum+=1
        colors[i] = [0,1,0,1]

print(sum)
print((contact_map_bool==-1).float().sum())
meshB.visual.vertex_colors = colors

tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tensor(inf)
tens

In [12]:
trimesh.Scene([meshB]).show()